# Ex1) P2P Task

In [1]:
from tasho.templates.P2P import P2P
from tasho import TaskModel, default_mpc_options
from tasho.templates.Regularization import Regularization
from tasho.Variable import Variable
from tasho.ConstraintExpression import ConstraintExpression
from tasho.Expression import Expression
from tasho.MPC import MPC 
from tasho import environment as env
from tasho import WorldSimulator
from tasho.OCPGenerator import OCPGenerator
from robotshyu import Robot as rob
from time import sleep
import numpy as np
import casadi as cs
import pybullet as p
import tasho
import robotshyu
import os

pybullet build time: May 20 2022 19:44:17


In [2]:
# Options for show frame
frame_enable = False

# Ex3) Nonholonomic Constraint

In [3]:
robot = rob.Robot("mmo_500_ppr")
link_name = 9

# Define initial conditions of the robot
q0_val = [-1.0, -0.523598, 1.5709, 3.14, 0, -0.523598, 0.0, 0.0, 0.0]
qd0_val = [0] * robot.ndof

################################################
# Task spacification - Approximation to object
################################################

# Select prediction horizon and sample time for the MPC execution
horizon_size = 10
t_mpc = 0.05

q_init = Variable(robot.name, 'q_init', 'parameter', (robot.ndof,1))
qd_init = Variable(robot.name, 'qd_init', 'parameter', (robot.ndof,1))
goal_pose = Variable(robot.name, "goal_pose", 'parameter', (4,4))
robot.set_joint_acceleration_limits(lb=-360*3.14159/180, ub=360*3.14159/180)

task_P2P = P2P(robot, link_name, goal_pose, q_init, 0.001)
task_P2P.write_task_graph("MMO500_P2P_Task4.svg")

Loading robot params from json ...
Loaded 9-DoF robot: mmo_500_ppr


In [4]:
print(q_init)
print(task_P2P.variables)

{'q_mmo_500_ppr': <tasho.Variable.Variable object at 0x7f6f8ff13760>, 'qd_mmo_500_ppr': <tasho.Variable.Variable object at 0x7f6f8ff13790>, 'qdd_mmo_500_ppr': <tasho.Variable.Variable object at 0x7f6f8ff13610>, 'q_init_mmo_500_ppr': <tasho.Variable.Variable object at 0x7f70341cc460>, 'goal_pose_mmo_500_ppr': <tasho.Variable.Variable object at 0x7f6f8ff1dfd0>}


In [5]:
task_P2P.remove_initial_constraints(task_P2P.constraint_expressions['stationary_qd_mmo_500_ppr'])
task_P2P.remove_terminal_constraints('rot_con_pose_9_mmo_500_ppr_vs_goal',
                                    'trans_con_pose_9_mmo_500_ppr_vs_goal')
task_P2P.write_task_graph("MMO500_P2P_Task5.svg")

In [6]:
task_P2P.add_initial_constraints(ConstraintExpression(robot.name, "eq", Expression(robot.name, "err_qd_qinit", lambda a, b : a - b, qd_init, task_P2P.variables['qd_mmo_500_ppr']),
                             "hard", reference = 0))
task_P2P.add_path_constraints(Regularization(task_P2P.expressions['trans_error_pose_9_mmo_500_ppr_vs_goal'], 2e0, norm = "L1"),
                            Regularization(task_P2P.expressions['ax_ang_error_pose_9_mmo_500_ppr_vs_goal'], 8e-1), 
                            Regularization(task_P2P.variables['qd_mmo_500_ppr'], 3e-2),
                            Regularization(task_P2P.variables['qdd_mmo_500_ppr'],4e-2))
task_P2P.add_path_constraints(ConstraintExpression(robot.name, "nonholonomic", Expression(robot.name, "nonholonomic", lambda a, b, c : a*cs.sin(c)-b*cs.cos(c), task_P2P.variables['q_mmo_500_ppr'], task_P2P.variables['qd_mmo_500_ppr']),
                             "hard", reference = 0))
task_P2P.write_task_graph("MMO500_P2P_Task6.svg")

In [7]:
pOCP = OCPGenerator(task_P2P, False, {"time_period":horizon_size*t_mpc, "horizon_steps":horizon_size})

tc = pOCP.tc

################################################
# Set solver and discretization options
################################################
# tc.set_ocp_solver("ipopt", {"ipopt": {"print_level": 5,"tol": 1e-3}})
# tc.set_ocp_solver("ipopt", {"ipopt": {"print_level": 0,"tol": 1e-3, "linear_solver":"ma27"}}) #use this if you have hsl
mpc_options = default_mpc_options.get_default_mpc_options()
tc.ocp_solver = mpc_options["ipopt_init"]['solver_name']
tc.ocp_options = mpc_options["ipopt_init"]["options"]
tc.set_ocp_solver(tc.ocp_solver, tc.ocp_options)

################################################
# Set parameter values
################################################
q = pOCP.stage_tasks[0].variables['q_mmo_500_ppr'].x
qd = pOCP.stage_tasks[0].variables['qd_mmo_500_ppr'].x
q_0 = pOCP.stage_tasks[0].variables['q_init_mmo_500_ppr'].x
qd_0 = pOCP.stage_tasks[0].variables['qd_init_mmo_500_ppr'].x
goal_pose = pOCP.stage_tasks[0].variables['goal_pose_mmo_500_ppr'].x
goal_pose_val =  cs.vertcat(
    cs.hcat([0, 1, 0, 0.5]),
    cs.hcat([1, 0, 0, 0.0]),
    cs.hcat([0, 0, -1, 0.25]),
    cs.hcat([0, 0, 0, 1]),
)
tc.set_initial(q, q0_val)
tc.set_value(goal_pose, goal_pose_val)
tc.set_value(q_0, q0_val)
tc.set_value(qd_0, qd0_val)

# Add an output port for joint velocities as well
tc.tc_dict["out_ports"].append({"name":"port_out_qd_mmo_500_ppr", "var":"qd_mmo_500_ppr", "desc": "output port for the joint velocities"})

# Add a monitor for termination criteria
tc.add_monitor({"name":"termination_criteria", "expression":cs.sqrt(cs.sumsqr(pOCP.stage_tasks[0].expressions["trans_error_pose_9_mmo_500_ppr_vs_goal"].x)) - 2e-2, "reference":0, "lower":True, "initial":True})

tc.mpc_solver = mpc_options["ipopt_lbfgs"]['solver_name']
tc.mpc_options = mpc_options["ipopt_lbfgs"]["options"]
os.system("export OMP_NUM_THREADS = 1")

sol = tc.solve_ocp()


******************************************************************************
This program contains Ipopt, a library for large-scale nonlinear optimization.
 Ipopt is released as open source code under the Eclipse Public License (EPL).
         For more information visit http://projects.coin-or.org/Ipopt
******************************************************************************

      solver  :   t_proc      (avg)   t_wall      (avg)    n_eval
    nlp_grad  |  73.00us ( 73.00us)  72.79us ( 72.79us)         1
  nlp_grad_f  |  52.00us ( 52.00us)  51.94us ( 51.94us)         1
   nlp_jac_g  |  12.00us ( 12.00us)  12.69us ( 12.69us)         1
       total  | 480.00us (480.00us) 473.67us (473.67us)         1


sh: 1: export: : bad variable name
CasADi - 2023-05-08 15:42:13 WARNING("NLP is overconstrained: There are 297 equality constraints but only 288 variables.") [.../casadi/core/nlpsol.cpp:511]


RuntimeError: Error in Opti::solve [OptiNode] at .../casadi/core/optistack.cpp:159:
.../casadi/core/optistack_internal.cpp:997: Assertion "return_success(accept_limit)" failed:
Solver failed. You may use opti.debug.value to investigate the latest values of variables. return_status is 'Not_Enough_Degrees_Of_Freedom'

In [9]:
dir_casadi_func = "casadi_dir"
os.makedirs("./"+dir_casadi_func, exist_ok=True)
vars_db = tc.generate_MPC_component("./"+dir_casadi_func+"/", {"ocp_cg_opts":{"save":True, "codegen":False, "jit":False}, "mpc":True, "mpc_cg_opts":{"save":True, "codegen":False, "jit":False}})

@1=(opti0_p_2[12:15]-fk_T(opti0_x_1){9}[12:15]), (sqrt(dot(@1, @1))-0.02)
@1=(opti0_p_2[12:15]-fk_T(opti0_x_1){9}[12:15]), (sqrt(dot(@1, @1))-0.02)


In [10]:
MPC_component = MPC("mmo_500_ppr_obj_pickup", "./"+dir_casadi_func+"/"+ tc.name + ".json")

In [10]:
obj = WorldSimulator.WorldSimulator(bullet_gui=True)

# Add robot to the world environment
position = [0.0, 0.0, 0.0]
orientation = [0.0, 0.0, 0.0, 1.0]
robotID = obj.add_robot(position, orientation, robot.name)
mmo500_frame_urdf = robotshyu.__path__[0]+"/robots/MMO_500/mmo500_description/mmo_500_ppr_frame.urdf"

if frame_enable==True:
    frameID0 = obj.add_robot(position,orientation,robot_urdf=mmo500_frame_urdf)
    frameID1 = obj.add_robot(position,orientation,robot_urdf=mmo500_frame_urdf)
    frameID2 = obj.add_robot(position,orientation,robot_urdf=mmo500_frame_urdf)
    frameID3 = obj.add_robot(position,orientation,robot_urdf=mmo500_frame_urdf)
    frameID4 = obj.add_robot(position,orientation,robot_urdf=mmo500_frame_urdf)
    frameID5 = obj.add_robot(position,orientation,robot_urdf=mmo500_frame_urdf)
    frameID6 = obj.add_robot(position,orientation,robot_urdf=mmo500_frame_urdf)
    frameID7 = obj.add_robot(position,orientation,robot_urdf=mmo500_frame_urdf)
    frameID8 = obj.add_robot(position,orientation,robot_urdf=mmo500_frame_urdf)
    frameID9 = obj.add_robot(position,orientation,robot_urdf=mmo500_frame_urdf)

    robotIDs=[frameID0, frameID1,frameID2,frameID3,frameID4,frameID5,frameID6,frameID7,frameID8,frameID9]

# Set environment
environment = env.Environment()
package_path = tasho.__path__[0]
cube1 = env.Cube(length = 1, position = [0.5, -0.2, 0.35], orientation = [0.0, 0.0, 0.0, 1.0], urdf = package_path+"/models/objects/cube_small.urdf")
environment.add_object(cube1, "cube")
table1 = env.Box(height = 0.3, position = [0.5, 0, 0], orientation = [0.0, 0.0, 0.7071080798594737, 0.7071054825112364], urdf =package_path+ "/models/objects/table.urdf")
environment.add_object(table1, "table1")

cube2 = env.Cube(length = 1, position = [0.5, -0.2, 0.35], orientation = [0.0, 0.0, 0.0, 1.0], urdf = package_path+"/models/objects/cube_small_col.urdf", fixed = True)
environment.add_object(cube2, "cube2")
environment.set_in_world_simulator(obj)
cubeID = environment.get_object_ID("cube")
cube2ID = environment.get_object_ID("cube2")

#p.resetBaseVelocity(cubeID, linearVelocity=[0, 0.8, 0])
# Determine number of samples that the simulation should be executed
no_samples = int(t_mpc / obj.physics_ts)
if no_samples != t_mpc / obj.physics_ts:
    print("[ERROR] MPC sampling time not integer multiple of physics sampling time")

# Correspondence between joint numbers in bullet and OCP
joint_indices = [0, 1, 2, 13, 14, 15, 16, 17, 18]

 # Begin the visualization by applying the initial control signal
ts, q_sol = tc.sol_sample(q, grid="control")
ts, q_dot_sol = tc.sol_sample(qd, grid="control")
if frame_enable==True:
    obj.resetMultiJointState(robotIDs, joint_indices, [q0_val])
    
obj.resetJointState(robotID,joint_indices,q0_val)
obj.setController(
    robotID, "velocity", joint_indices, targetVelocities=q_dot_sol[0]
)

q_log = []
q_dot_log = []
predicted_pos_log = []
q_pred = [0]*horizon_size

In [ ]:
# Execute the MPC loop

p.resetBaseVelocity(cubeID, linearVelocity=[0, 1, 0])

for i in range(horizon_size * 100):
    print("----------- MPC execution -----------")

    q_now = obj.readJointPositions(robotID, joint_indices)
    qd_now = obj.readJointVelocities(robotID, joint_indices)
        
    MPC_component.input_ports["port_inp_q_init_mmo_500_ppr"]["val"] = q_now
    MPC_component.input_ports["port_inp_qd_init_mmo_500_ppr"]["val"] = qd_now

    # Predict the position of the target object (cube)
    lin_vel, ang_vel = p.getBaseVelocity(cubeID)
    lin_vel = cs.DM(lin_vel)
    lin_pos, _ = p.getBasePositionAndOrientation(cubeID)
    lin_pos = cs.DM(lin_pos)
    time_to_stop = cs.norm_1(lin_vel) / 0.3
    predicted_pos = (
        cs.DM(lin_pos)
        + cs.DM(lin_vel) * time_to_stop
        - 0.5 * 0.5 * lin_vel / (cs.norm_1(lin_vel) + 1e-3) * time_to_stop ** 2
    )
    predicted_pos_log.append(predicted_pos.full())
    p.resetBasePositionAndOrientation(cube2ID, predicted_pos.full(), [0.0, 0.0, 0.0, 1.0])
    predicted_pos[2] += 0.06  # cube height
    print("Predicted position of cube", predicted_pos)
    predicted_pos_val = cs.vertcat(
        cs.hcat([0, 0, 1, predicted_pos[0]]),
        cs.hcat([0, 1, 0, predicted_pos[1]]),
        cs.hcat([-1, 0, 0, predicted_pos[2]]),
        cs.hcat([0, 0, 0, 1]),
    )

    MPC_component.input_ports["port_inp_goal_pose_mmo_500_ppr"]["val"] = cs.vec(predicted_pos_val)
        
    if i == 0:
        MPC_component.configMPC()

    MPC_component.runMPC()
    if frame_enable==True:
        sol = MPC_component.res_vals
        for i in range(horizon_size):
            q_pred[i]=sol[robot.ndof*i:robot.ndof*i+robot.ndof].full()
        obj.resetMultiJointState(robotIDs[1:], joint_indices, q_pred)

    q_log.append(q_now)
    q_dot_log.append(qd_now)

    # Set control signal to the simulated robot
    qd_control_sig = MPC_component.output_ports["port_out_qd_mmo_500_ppr"]["val"].full()
    qdd_control_sig = (MPC_component.output_ports["port_out_qdd_mmo_500_ppr"]["val"] * t_mpc).full()
    obj.setController(
        robotID, "velocity", joint_indices, targetVelocities=qd_control_sig + qdd_control_sig
    )

    # Simulate
    obj.run_simulation(no_samples)
#     sleep(0.1)

    # Termination criteria
#     if "termination_criteria_true" in MPC_component.event_output_port:
#         break

----------- MPC execution -----------
Predicted position of cube [0.5, 0.35833055833056, 0.41]
This is Ipopt version 3.12.7, running with linear solver ma27.

Number of nonzeros in equality constraint Jacobian...:      657
Number of nonzeros in inequality constraint Jacobian.:      270
Number of nonzeros in Lagrangian Hessian.............:        0

Total number of variables............................:      288
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:      207
Total number of inequality constraints...............:      270
        inequality constraints with only lower bounds:        0
   inequality constraints with lower and upper bounds:      270
        inequality constraints with only upper bounds:        0

iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg) alpha_du alp

----------- MPC execution -----------
Predicted position of cube [0.5, 0.98659197217692, -0.71193226588251]
This is Ipopt version 3.12.7, running with linear solver ma27.

Number of nonzeros in equality constraint Jacobian...:      657
Number of nonzeros in inequality constraint Jacobian.:      270
Number of nonzeros in Lagrangian Hessian.............:        0

Total number of variables............................:      288
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:      207
Total number of inequality constraints...............:      270
        inequality constraints with only lower bounds:        0
   inequality constraints with lower and upper bounds:      270
        inequality constraints with only upper bounds:        0

iter    objective    inf_pr   inf_du lg(mu)  ||d||  lg(rg)

----------- MPC execution -----------
Predicted position of cube [0.50000014555438, 0.45143207403506, 0.27496429375773]
This is Ipopt version 3.12.7, running with linear solver ma27.

Number of nonzeros in equality constraint Jacobian...:      657
Number of nonzeros in inequality constraint Jacobian.:      270
Number of nonzeros in Lagrangian Hessian.............:        0

Total number of variables............................:      288
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:      207
Total number of inequality constraints...............:      270
        inequality constraints with only lower bounds:        0
   inequality constraints with lower and upper bounds:      270
        inequality constraints with only upper bounds:        0

iter    objective    inf_pr   inf_du lg(mu)  |

----------- MPC execution -----------
Predicted position of cube [0.50000017503029, 0.49627097282024, 0.27259912220433]
This is Ipopt version 3.12.7, running with linear solver ma27.

Number of nonzeros in equality constraint Jacobian...:      657
Number of nonzeros in inequality constraint Jacobian.:      270
Number of nonzeros in Lagrangian Hessian.............:        0

Total number of variables............................:      288
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:      207
Total number of inequality constraints...............:      270
        inequality constraints with only lower bounds:        0
   inequality constraints with lower and upper bounds:      270
        inequality constraints with only upper bounds:        0

iter    objective    inf_pr   inf_du lg(mu)  |

----------- MPC execution -----------
Predicted position of cube [0.50000027674752, 0.72526208028064, -0.0024699124857075]
This is Ipopt version 3.12.7, running with linear solver ma27.

Number of nonzeros in equality constraint Jacobian...:      657
Number of nonzeros in inequality constraint Jacobian.:      270
Number of nonzeros in Lagrangian Hessian.............:        0

Total number of variables............................:      288
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:      207
Total number of inequality constraints...............:      270
        inequality constraints with only lower bounds:        0
   inequality constraints with lower and upper bounds:      270
        inequality constraints with only upper bounds:        0

iter    objective    inf_pr   inf_du lg(mu)

...

----------- MPC execution -----------
Predicted position of cube [0.49988145929185, 0.91597839604952, 0.084988291479343]
This is Ipopt version 3.12.7, running with linear solver ma27.

Number of nonzeros in equality constraint Jacobian...:      657
Number of nonzeros in inequality constraint Jacobian.:      270
Number of nonzeros in Lagrangian Hessian.............:        0

Total number of variables............................:      288
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:      207
Total number of inequality constraints...............:      270
        inequality constraints with only lower bounds:        0
   inequality constraints with lower and upper bounds:      270
        inequality constraints with only upper bounds:        0

iter    objective    inf_pr   inf_du lg(mu)  

----------- MPC execution -----------
Predicted position of cube [0.49988145929185, 0.91597839604952, 0.084988291479343]
This is Ipopt version 3.12.7, running with linear solver ma27.

Number of nonzeros in equality constraint Jacobian...:      657
Number of nonzeros in inequality constraint Jacobian.:      270
Number of nonzeros in Lagrangian Hessian.............:        0

Total number of variables............................:      288
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:      207
Total number of inequality constraints...............:      270
        inequality constraints with only lower bounds:        0
   inequality constraints with lower and upper bounds:      270
        inequality constraints with only upper bounds:        0

iter    objective    inf_pr   inf_du lg(mu)  

----------- MPC execution -----------
Predicted position of cube [0.49988145929185, 0.91597839604952, 0.084988291479343]
This is Ipopt version 3.12.7, running with linear solver ma27.

Number of nonzeros in equality constraint Jacobian...:      657
Number of nonzeros in inequality constraint Jacobian.:      270
Number of nonzeros in Lagrangian Hessian.............:        0

Total number of variables............................:      288
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:      207
Total number of inequality constraints...............:      270
        inequality constraints with only lower bounds:        0
   inequality constraints with lower and upper bounds:      270
        inequality constraints with only upper bounds:        0

iter    objective    inf_pr   inf_du lg(mu)  

----------- MPC execution -----------
Predicted position of cube [0.49988145929185, 0.91597839604952, 0.084988291479343]
This is Ipopt version 3.12.7, running with linear solver ma27.

Number of nonzeros in equality constraint Jacobian...:      657
Number of nonzeros in inequality constraint Jacobian.:      270
Number of nonzeros in Lagrangian Hessian.............:        0

Total number of variables............................:      288
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:      207
Total number of inequality constraints...............:      270
        inequality constraints with only lower bounds:        0
   inequality constraints with lower and upper bounds:      270
        inequality constraints with only upper bounds:        0

iter    objective    inf_pr   inf_du lg(mu)  

----------- MPC execution -----------
Predicted position of cube [0.49988145929185, 0.91597839604952, 0.084988291479343]
This is Ipopt version 3.12.7, running with linear solver ma27.

Number of nonzeros in equality constraint Jacobian...:      657
Number of nonzeros in inequality constraint Jacobian.:      270
Number of nonzeros in Lagrangian Hessian.............:        0

Total number of variables............................:      288
                     variables with only lower bounds:        0
                variables with lower and upper bounds:        0
                     variables with only upper bounds:        0
Total number of equality constraints.................:      207
Total number of inequality constraints...............:      270
        inequality constraints with only lower bounds:        0
   inequality constraints with lower and upper bounds:      270
        inequality constraints with only upper bounds:        0

iter    objective    inf_pr   inf_du lg(mu)  

In [ ]:
obj.end_simulation()

max(MPC_component.solver_times)